## Train step 1: Bootstrap from pretrained model

In [ ]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

%load_ext autoreload
%autoreload 2
%matplotlib notebook

import pickle, os, warnings, sys, random, logging, librosa, json, nemo
warnings.filterwarnings("ignore")
logger = logging.getLogger()
logger.setLevel(logging.INFO)

from Cfg import Cfg
from reshuffle_samples import reshuffle_samples
import nemo.collections.asr as nemo_asr
from load_recent import load_recent
from ruamel.yaml import YAML

from omegaconf import DictConfig
import os, datetime
from load_pretrained_amharic_model import load_pretrained_amharic_model

In [ ]:
C, model, params = load_pretrained_amharic_model()

## Train Phase 2: K-fold validation more or less

In [ ]:
import pytorch_lightning as pl
import os, datetime
from Cfg import Cfg
from load_pretrained_amharic_model import load_pretrained_amharic_model
C, model, params = load_pretrained_amharic_model()

In [11]:
model_save_dir='save/nemo_amharic'

class ModelCheckpointAtEpochEnd(pl.callbacks.ModelCheckpoint):
    def on_epoch_end(self, trainer, pl_module):
        metrics = trainer.callback_metrics
        metrics['epoch'] = trainer.current_epoch
        trainer.checkpoint_callback.on_validation_end(trainer, pl_module)

pid=os.getpid()
dt=datetime.datetime.now().strftime("%Y%m%d_%H%M%S")

checkpoint_callback = ModelCheckpointAtEpochEnd(
    filepath=model_save_dir+'/amharic_'+f'{dt}_{pid}'+'_{epoch:02d}',
    verbose=True,
    save_top_k=-1,
    save_weights_only=False,
    period=1)

trainer = pl.Trainer(gpus=[0], max_epochs=200, amp_level='O1', precision=16, checkpoint_callback=checkpoint_callback)

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
CUDA_VISIBLE_DEVICES: [0]
Using native 16bit precision.


In [44]:
from reshuffle_samples import reshuffle_samples
reshuffle_samples(C)

In [45]:
trainer.fit(model)

[NeMo I 2020-10-15 10:28:49 modelPT:572] Optimizer config = Novograd (
    Parameter Group 0
        amsgrad: False
        betas: [0.8, 0.5]
        eps: 1e-08
        grad_averaging: False
        lr: 0.001
        weight_decay: 0.001
    )


[NeMo W 2020-10-15 10:28:49 lr_scheduler:526] Neither `max_steps` nor `iters_per_batch` were provided to `optim.sched`, cannot compute effective `max_steps` !
    Scheduler will not be instantiated !

  | Name              | Type                              | Params
------------------------------------------------------------------------
0 | preprocessor      | AudioToMelSpectrogramPreprocessor | 0     
1 | encoder           | ConvASREncoder                    | 18 M  
2 | spec_augmentation | SpectrogramAugmentation           | 0     
3 | _wer              | WER                               | 0     
4 | decoder           | ConvASRDecoder                    | 241 K 
5 | loss              | CTCLoss                           | 0     


[NeMo I 2020-10-15 10:28:50 wer:148] 
    
[NeMo I 2020-10-15 10:28:50 wer:149] reference:ደውሎ አንተ ሚስትህ እንደዚህ እንደዚህ ብሎ ነግሮታል ለካ ነግሮኝ ነው ነገረኝ በለሳ መግባትሽን ምናምን ሲል አዎ
[NeMo I 2020-10-15 10:28:50 wer:150] decoded  :ደውሎ አንተ ግን እንደዚህ እንደሚጣ እነዞታለች ነግሮለ ክሬ ንበለ ታመዛችሁ ንግ


[NeMo I 2020-10-15 10:28:50 wer:148] 
    
[NeMo I 2020-10-15 10:28:50 wer:149] reference:አዎ እኛ የምንሰራበት ቦታ ላይ ኦቨር ታይም የለም ያው ውስጥ እንትን ግን ከገባህ
[NeMo I 2020-10-15 10:28:50 wer:150] decoded  :አዎ እኛ የምንሰራበት ቦታ ላይ ኦቨር ታይም የለም ያው ውስጥ እንትን ግን ከገባህ
[NeMo I 2020-10-15 10:28:50 wer:148] 
    
[NeMo I 2020-10-15 10:28:50 wer:149] reference:ኧረ እባክህ
[NeMo I 2020-10-15 10:28:50 wer:150] decoded  :ኧረ እባክህ
[NeMo I 2020-10-15 10:28:50 wer:148] 
    
[NeMo I 2020-10-15 10:28:50 wer:149] reference:አዎ ሰላም ነን
[NeMo I 2020-10-15 10:28:50 wer:150] decoded  :አዎ ሰላም ነን
[NeMo I 2020-10-15 10:28:51 wer:148] 
    
[NeMo I 2020-10-15 10:28:51 wer:149] reference:ወደ ይሰማል
[NeMo I 2020-10-15 10:28:51 wer:150] decoded  :ወደ አማን
[NeMo I 2020-10-15 10:28:51 wer:148] 
    
[NeMo I 2020-10-15 10:28:51 wer:149] reference:እ
[NeMo I 2020-10-15 10:28:51 wer:150] decoded  :እ
[NeMo I 2020-10-15 10:28:51 wer:148] 
    
[NeMo I 2020-10-15 10:28:51 wer:149] reference:ቆይ ለምን አንተ አላደርክም ነበር እነ እሱ ጋር
[NeMo I 2020-10-15 10:28:51 wer:150

[NeMo I 2020-10-15 10:29:06 wer:148] 
    
[NeMo I 2020-10-15 10:29:06 wer:149] reference:እ ስማ እንጂ
[NeMo I 2020-10-15 10:29:06 wer:150] decoded  :እ ስማ እንጂ
[NeMo I 2020-10-15 10:29:06 wer:148] 
    
[NeMo I 2020-10-15 10:29:06 wer:149] reference:እኔ እደውልለታለሁ በቃ ስንገናኝ ማለት ነው አንቺና እኔ
[NeMo I 2020-10-15 10:29:06 wer:150] decoded  :እኔ እደውልለታለሁ በእቃ ስንገናኝ ማለት ነው አንቺና እኔ
[NeMo I 2020-10-15 10:29:07 wer:148] 
    
[NeMo I 2020-10-15 10:29:07 wer:149] reference:ም ምናልባት በሚቀጥለው ልትመጣ ትችላለች ወይ ደግሞ እኔ እና አንተ አንዱን ቀን እንሄዳለን በ
[NeMo I 2020-10-15 10:29:07 wer:150] decoded  :ም ምናልባት በሚቀጥለው ልትመጣ ትችላለች ወይ ደግሞ እኔ እና አንተ አንዱን ቀን እንሄዳለን በ
[NeMo I 2020-10-15 10:29:07 wer:148] 
    
[NeMo I 2020-10-15 10:29:07 wer:149] reference:ምንም አይደል አንቺ ደህና ነሽ
[NeMo I 2020-10-15 10:29:07 wer:150] decoded  :ምንም ል አንቺ ደህና ነሽ
[NeMo I 2020-10-15 10:29:07 wer:148] 
    
[NeMo I 2020-10-15 10:29:07 wer:149] reference:ስም ነገር ሞክር እስኪ ማንዴላ
[NeMo I 2020-10-15 10:29:07 wer:150] decoded  :ስም ነገር ሞክር እስኪ ማንዴላ
[NeMo I 2020-10-15 10:29:08

...

[NeMo I 2020-10-15 12:05:02 wer:148] 
    
[NeMo I 2020-10-15 12:05:02 wer:149] reference:ደውሎ አንተ ሚስትህ እንደዚህ እንደዚህ ብሎ ነግሮታል ለካ ነግሮኝ ነው ነገረኝ በለሳ መግባትሽን ምናምን ሲል አዎ
[NeMo I 2020-10-15 12:05:02 wer:150] decoded  :ደውሎ አንተን ግን እንደዚህ ንሚቀኝ  እነበታለች  ነግሮ ክሬንበለሳመጣች
[NeMo I 2020-10-15 12:05:02 wer:148] 
    
[NeMo I 2020-10-15 12:05:02 wer:149] reference:አዎ ከእዚያ በኋላ ትዕግስት ከእዚያ ደውላ ስልኩን አንስቶላት ነው የት እንደሆነ ሊነግረን የቻለው
[NeMo I 2020-10-15 12:05:02 wer:150] decoded  :አዎ ከእዛ በኋላ ትግስት ከእዛ ደውላ ስልኩን አንስጠላትነውየቴ እንደሆነ የልነግራን ቻለ
[NeMo I 2020-10-15 12:05:02 wer:148] 
    
[NeMo I 2020-10-15 12:05:02 wer:149] reference:ኧረ ስለ እሷ አልጠየኩም ይህን እኮ አስረበብ ናትኝ እንደዚህ እንደዚህ ነው እያለችኝ ስለወርቄ አልጠየኳትም እሷም ያው የሆነ ሥራ ተወዳድራ አልፋ
[NeMo I 2020-10-15 12:05:02 wer:150] decoded  :ኧረ ስለሱ አልጠየኩም እን እኮ አስረበም ላት ይባለፈው ደውላ አንደዚህ እንደዚህ ነው አለችኝ ሱጌ አልጠየኳትም ሷሚ የሆነ ሥራተ ወደግራንፈ
[NeMo I 2020-10-15 12:05:02 wer:148] 
    
[NeMo I 2020-10-15 12:05:02 wer:149] reference:አዎ አንተ አንተ እኮ እልም ብለህ ጠፋህ እኮ አሁን እኮ ግራ ነው የሚገባኝ እኮ የሆነ ብቅ ብለህ እንኳን ታይተህ ምናምን አትመለስም

[NeMo I 2020-10-15 12:05:06 wer:150] decoded  :እንደ በጣም ኮባለሁ
[NeMo I 2020-10-15 12:05:06 wer:148] 
    
[NeMo I 2020-10-15 12:05:06 wer:149] reference:አዎ ይሰማኛል እኔም ኔትዎርክ ምናም ኔትዎርክ ምናምን ከተጨናነቀ እየተንቀሳቀስክ እንዳትዘጋው እንዳ እንዳይቋረጥ
[NeMo I 2020-10-15 12:05:06 wer:150] decoded  :አዎ ይሰማ ሰ ራ መሱናምን ሰተጭናተካልራክ እንትዘበውብኝ እንዳይቋረውቱ
[NeMo I 2020-10-15 12:05:06 wer:148] 
    
[NeMo I 2020-10-15 12:05:06 wer:149] reference:አዎ
[NeMo I 2020-10-15 12:05:06 wer:150] decoded  :አዎ
[NeMo I 2020-10-15 12:05:06 wer:148] 
    
[NeMo I 2020-10-15 12:05:06 wer:149] reference:አዎ እያለፈ ነው ክረምቱ እንደ ይባል የለ እንደ ቡሄ ካለፈ የለም ክረምት
[NeMo I 2020-10-15 12:05:06 wer:150] decoded  :አዎ እያነፈ ነው ግረውሁንቱ እንደ ይት ባልለ እንዲ ውይ ካለፈ የለም ክራምሽ
[NeMo I 2020-10-15 12:05:06 wer:148] 
    
[NeMo I 2020-10-15 12:05:06 wer:149] reference:ሄሎ ይሰማኛል ድምፅሽ
[NeMo I 2020-10-15 12:05:06 wer:150] decoded  :ሄሎ ይሰማኛል ደንብ
[NeMo I 2020-10-15 12:05:07 wer:148] 
    
[NeMo I 2020-10-15 12:05:07 wer:149] reference:ዊ በጣም አስቸጋሪ ነው ሠራተኛ እኮ በጣም ከባድ ነው አሁን
[NeMo I 2020-10-15 

[NeMo I 2020-10-15 12:05:10 wer:148] 
    
[NeMo I 2020-10-15 12:05:10 wer:149] reference:አዎ እምትፈልገውን ነገር መተህ አገልግሎት ማግኘት ትችላለህ
[NeMo I 2020-10-15 12:05:10 wer:150] decoded  :አዎ የምትፈልገውን ነገር መት አገለት ማግኘት ይችላለህ
[NeMo I 2020-10-15 12:05:10 wer:148] 
    
[NeMo I 2020-10-15 12:05:10 wer:149] reference:አዎ ስድስት መቶ ብር ከፍለህ ትጀምራለህ በቃ ብድር
[NeMo I 2020-10-15 12:05:10 wer:150] decoded  :አዎ ስልስት መኮው በር ፍለስገ በቃ ብ
[NeMo I 2020-10-15 12:05:10 wer:148] 
    
[NeMo I 2020-10-15 12:05:10 wer:149] reference:አንዳንዴ
[NeMo I 2020-10-15 12:05:10 wer:150] decoded  :ምንደ አንዴ
[NeMo I 2020-10-15 12:05:11 wer:148] 
    
[NeMo I 2020-10-15 12:05:11 wer:149] reference:ሁሉም አሪፍ ነው በዐል እንደት ነበር
[NeMo I 2020-10-15 12:05:11 wer:150] decoded  :ሁሉም አሪፍ ነው አዐል እንደት ነበ
[NeMo I 2020-10-15 12:05:11 wer:148] 
    
[NeMo I 2020-10-15 12:05:11 wer:149] reference:የምትመጣ መስሎኝ ነው
[NeMo I 2020-10-15 12:05:11 wer:150] decoded  :በጣም ውሌንም
[NeMo I 2020-10-15 12:05:11 wer:148] 
    
[NeMo I 2020-10-15 12:05:11 wer:149] reference:የ ተቃርቧል ምና


Epoch 00199: saving model to /home/catskills/Desktop/openasr20/save/nemo_amharic/amharic_20201015_005720_353924_epoch=199.ckpt


1

## Local test on BUILD -- In Sample

In [16]:
from json_lines_load import json_lines_load
T=json_lines_load(f'{C.build_dir}/train_manifest.json')
V=json_lines_load(f'{C.build_dir}/test_manifest.json')
samples=T+V

len(samples)

S=list(sorted([(x['audio_filepath'],x['text']) for x in samples]))

audio_files=[x for x,y in S[0:12]]
transcripts=[y for x,y in S[0:12]]

pred=model.transcribe(paths2audio_files=audio_files, batch_size=1)

import pandas as pd
pd.DataFrame(zip(transcripts,pred), columns=['gold','pred'])

[NeMo I 2020-10-15 09:29:20 collections:173] Dataset loaded with 12 files totalling 333.33 hours
[NeMo I 2020-10-15 09:29:20 collections:174] 0 files were filtered totalling 0.00 hours


gold                                 pred
0            አዎ እኔ አጋጣሚ አጭር ቀጠሮ ነበረችኝ እ           አዎ እኔ አጋጣሚ አጭር ቀጠሮ ነበረችኝ እ
1      አዎ ኑሯቸው ነዋ እንደ እኛ አቧራ እያቦነኑ አላደጉ     አዎ ኑሯቸው ነዋ እንደ እኛ አቧራ እያቦነኑ አላደጉ
2        ታድያ ምን ላደርግ ትምህርቱ እንደት ነው የማታው       ታድያ ምን ላደርግ ትምህርቱ እንደት ነው የማታው
3                       ከሥራው ጋር ሄደልህ ግን                        ሥራው ጋር ሄደልግህን
4                          ከሥራው ጋር ሄደልህ                         ከሥራው ጋር ሄደልህ
5     አይ አጣጥሞ መያዝ ነው በኋላ እሱ የሚያዋጣው ሲያልቅ  አይ አጣጥመ እኔው የያዝ ነው በኋላ እሱንን ያዋጣቴያልክ
6                   አዲስ ሥራ ነው የገባኸው እንደ                  አዲስ ሥራ ነው የገባኸው እንደ
7                                 የት ነው                                የት ነው
8                                     እ                                    እ
9               ምን ጊዜያዊ ነው ኤርፖርት ወይስ ቋሚ              ምን ጊዜያዊ ነው ኤርፖርት ወይስ ቋሚ
10  ምን ሥራው አዎ አየር መንገድ እኮ ክፍያው ጥሩ እኮ ነው  ምን ሥራው አዎ አየር መንገድ እኮ ክፍያው ጥሩ እኮ ነው
11  አዎ ግን የፖኬት መኒ ምናምን የኪስ ገንዘብ ያስብሏቸዋል   አዎ ግን ያዎው ፐኬት መን ምናምን ኦኪከዛ አስቡላችኋም

## With save/restore

In [43]:
model3 = nemo_asr.models.EncDecCTCModel.load_from_checkpoint('save/nemo_amharic/amharic_20201015_005720_353924_epoch=167.ckpt')
model3.cuda(0)
pred3=model3.transcribe(paths2audio_files=audio_files, batch_size=1)
pd.DataFrame(zip(transcripts,pred3), columns=['gold','pred'])

[NeMo W 2020-10-15 10:18:03 modelPT:102] Please call the ModelPT.setup_training_data() method and provide a valid configuration file to setup the train data loader.
    Train config : 
    manifest_filepath: NIST/openasr20_amharic/build/train_manifest.json
    sample_rate: 16000
    labels:
    - ' '
    - ሀ
    - ሁ
    - ሂ
    - ሃ
    - ሄ
    - ህ
    - ሆ
    - ለ
    - ሉ
    - ሊ
    - ላ
    - ሌ
    - ል
    - ሎ
    - ሏ
    - ሐ
    - ሑ
    - ሒ
    - ሔ
    - ሕ
    - መ
    - ሙ
    - ሚ
    - ማ
    - ሜ
    - ም
    - ሞ
    - ሟ
    - ሠ
    - ሡ
    - ሣ
    - ሥ
    - ሦ
    - ረ
    - ሩ
    - ሪ
    - ራ
    - ሬ
    - ር
    - ሮ
    - ሯ
    - ሰ
    - ሱ
    - ሲ
    - ሳ
    - ሴ
    - ስ
    - ሶ
    - ሷ
    - ሸ
    - ሹ
    - ሺ
    - ሻ
    - ሼ
    - ሽ
    - ሾ
    - ሿ
    - ቀ
    - ቁ
    - ቂ
    - ቃ
    - ቄ
    - ቅ
    - ቆ
    - ቋ
    - በ
    - ቡ
    - ቢ
    - ባ
    - ቤ
    - ብ
    - ቦ
    - ቧ
    - ቨ
    - ቪ
    - ቫ
    - ቬ
    - ቭ
    - ተ
    - ቱ
    - ቲ
    - ታ
    - ቴ
    - ት
    - ቶ
    - ቷ
    - ቸ
  

[NeMo I 2020-10-15 10:18:03 features:241] PADDING: 16
[NeMo I 2020-10-15 10:18:03 features:258] STFT using torch
[NeMo I 2020-10-15 10:18:04 collections:173] Dataset loaded with 12 files totalling 333.33 hours
[NeMo I 2020-10-15 10:18:04 collections:174] 0 files were filtered totalling 0.00 hours


gold                                 pred
0            አዎ እኔ አጋጣሚ አጭር ቀጠሮ ነበረችኝ እ           አዎ እኔ አጋጣሚ አጭር ቀጠሮ ነበረችኝ እ
1      አዎ ኑሯቸው ነዋ እንደ እኛ አቧራ እያቦነኑ አላደጉ     አዎ ኑሯቸው ነዋ እንደ እኛ አቧራ እያቦነኑ አላደጉ
2        ታድያ ምን ላደርግ ትምህርቱ እንደት ነው የማታው       ታድያ ምን ላደርግ ትምህርቱ እንደት ነው የማታው
3                       ከሥራው ጋር ሄደልህ ግን                        ሥራው ጋር ሄደልግህን
4                          ከሥራው ጋር ሄደልህ                         ከሥራው ጋር ሄደልህ
5     አይ አጣጥሞ መያዝ ነው በኋላ እሱ የሚያዋጣው ሲያልቅ  አይ አጣጥመ እነው የያዝ ነው በኋላ እሱንን ያዋጣቴያልክ
6                   አዲስ ሥራ ነው የገባኸው እንደ                  አዲስ ሥራ ነው የገባኸው እንደ
7                                 የት ነው                                የት ነው
8                                     እ                                    እ
9               ምን ጊዜያዊ ነው ኤርፖርት ወይስ ቋሚ              ምን ጊዜያዊ ነው ኤርፖርት ወይስ ቋሚ
10  ምን ሥራው አዎ አየር መንገድ እኮ ክፍያው ጥሩ እኮ ነው  ምን ሥራው አዎ አየር መንገድ እኮ ክፍያው ጥሩ እኮ ነው
11  አዎ ግን የፖኬት መኒ ምናምን የኪስ ገንዘብ ያስብሏቸዋል    አዎ ግሪ ያው ፐኬት መኝ ምናምን ኦስከዛ አስቡላችኋም

## Local test on BUILD -- Out of Sample

## Do a silence split on DEV

In [ ]:
from Cfg import Cfg
C = Cfg('NIST', 16000, 'amharic', 'dev') 

from RecordingCorpus import RecordingCorpus
from multiprocessing import Pool

if __name__ == '__main__':
    with Pool(16) as pool:
        recordings = RecordingCorpus(C, pool)

from SplitCorpus import SplitCorpus
ssplits=SplitCorpus.split_on_silence(C, recordings, 30)

import soundfile as sf
from tqdm.auto import tqdm
F=[]
for sample in tqdm(ssplits.artifacts):
    (_,root,(start,end))=sample.key
    audio = sample.source.value
    audio_path=f'{C.audio_split_dir}/{root}_{start}_{end}.wav'
    sf.write(audio_path, audio, C.sample_rate)
    sample.source.filename=audio_path
    F.append(audio_path)

## Transcribe DEV

In [1]:
from load_pretrained_amharic_model import load_pretrained_amharic_model
from glob import glob
import pickle, os, warnings, sys, random, logging, librosa, json, nemo
warnings.filterwarnings("ignore")
logger = logging.getLogger()
logger.setLevel(logging.INFO)

[NeMo W 2020-10-15 00:51:09 experimental:28] Module <class 'nemo.collections.asr.data.audio_to_text.AudioToCharDataset'> is experimental, not ready for production and is not fully supported. Use at your own risk.
[NeMo W 2020-10-15 00:51:09 experimental:28] Module <class 'nemo.collections.asr.data.audio_to_text.AudioToBPEDataset'> is experimental, not ready for production and is not fully supported. Use at your own risk.
[NeMo W 2020-10-15 00:51:09 experimental:28] Module <class 'nemo.collections.asr.data.audio_to_text.AudioLabelDataset'> is experimental, not ready for production and is not fully supported. Use at your own risk.
[NeMo W 2020-10-15 00:51:09 experimental:28] Module <class 'nemo.collections.asr.data.audio_to_text._TarredAudioToTextDataset'> is experimental, not ready for production and is not fully supported. Use at your own risk.
[NeMo W 2020-10-15 00:51:09 experimental:28] Module <class 'nemo.collections.asr.data.audio_to_text.TarredAudioToCharDataset'> is experimental,

In [2]:
C, model, params = load_pretrained_amharic_model()

[NeMo I 2020-10-15 00:51:11 cloud:55] Found existing object /home/catskills/.cache/torch/NeMo/NeMo_1.0.0b1/QuartzNet15x5Base-En/00869f9c89b8393ca3de640e0c536bd2/QuartzNet15x5Base-En.nemo.
[NeMo I 2020-10-15 00:51:11 cloud:61] Re-using file from: /home/catskills/.cache/torch/NeMo/NeMo_1.0.0b1/QuartzNet15x5Base-En/00869f9c89b8393ca3de640e0c536bd2/QuartzNet15x5Base-En.nemo
[NeMo I 2020-10-15 00:51:11 common:394] Instantiating model from pre-trained checkpoint
[NeMo I 2020-10-15 00:51:11 features:241] PADDING: 16
[NeMo I 2020-10-15 00:51:11 features:258] STFT using torch
[NeMo I 2020-10-15 00:51:13 modelPT:237] Model EncDecCTCModel was successfully restored from /home/catskills/.cache/torch/NeMo/NeMo_1.0.0b1/QuartzNet15x5Base-En/00869f9c89b8393ca3de640e0c536bd2/QuartzNet15x5Base-En.nemo.
[NeMo I 2020-10-15 00:51:13 ctc_models:189] Changed decoder to output to [' ', 'ሀ', 'ሁ', 'ሂ', 'ሃ', 'ሄ', 'ህ', 'ሆ', 'ለ', 'ሉ', 'ሊ', 'ላ', 'ሌ', 'ል', 'ሎ', 'ሏ', 'ሐ', 'ሑ', 'ሒ', 'ሔ', 'ሕ', 'መ', 'ሙ', 'ሚ', 'ማ', 'ሜ', '

[NeMo W 2020-10-15 00:51:13 lr_scheduler:526] Neither `max_steps` nor `iters_per_batch` were provided to `optim.sched`, cannot compute effective `max_steps` !
    Scheduler will not be instantiated !


[NeMo I 2020-10-15 00:51:13 collections:173] Dataset loaded with 7464 files totalling 7.67 hours
[NeMo I 2020-10-15 00:51:13 collections:174] 0 files were filtered totalling 0.00 hours
[NeMo I 2020-10-15 00:51:13 collections:173] Dataset loaded with 1866 files totalling 1.87 hours
[NeMo I 2020-10-15 00:51:13 collections:174] 0 files were filtered totalling 0.00 hours


[NeMo W 2020-10-15 00:51:14 modelPT:102] Please call the ModelPT.setup_training_data() method and provide a valid configuration file to setup the train data loader.
    Train config : 
    manifest_filepath: NIST/openasr20_amharic/build/train_manifest.json
    sample_rate: 16000
    labels:
    - ' '
    - ሀ
    - ሁ
    - ሂ
    - ሃ
    - ሄ
    - ህ
    - ሆ
    - ለ
    - ሉ
    - ሊ
    - ላ
    - ሌ
    - ል
    - ሎ
    - ሏ
    - ሐ
    - ሑ
    - ሒ
    - ሔ
    - ሕ
    - መ
    - ሙ
    - ሚ
    - ማ
    - ሜ
    - ም
    - ሞ
    - ሟ
    - ሠ
    - ሡ
    - ሣ
    - ሥ
    - ሦ
    - ረ
    - ሩ
    - ሪ
    - ራ
    - ሬ
    - ር
    - ሮ
    - ሯ
    - ሰ
    - ሱ
    - ሲ
    - ሳ
    - ሴ
    - ስ
    - ሶ
    - ሷ
    - ሸ
    - ሹ
    - ሺ
    - ሻ
    - ሼ
    - ሽ
    - ሾ
    - ሿ
    - ቀ
    - ቁ
    - ቂ
    - ቃ
    - ቄ
    - ቅ
    - ቆ
    - ቋ
    - በ
    - ቡ
    - ቢ
    - ባ
    - ቤ
    - ብ
    - ቦ
    - ቧ
    - ቨ
    - ቪ
    - ቫ
    - ቬ
    - ቭ
    - ተ
    - ቱ
    - ቲ
    - ታ
    - ቴ
    - ት
    - ቶ
    - ቷ
    - ቸ
  

[NeMo I 2020-10-15 00:51:14 features:241] PADDING: 16
[NeMo I 2020-10-15 00:51:14 features:258] STFT using torch


In [3]:
files=list(sorted(glob(f'{C.audio_split_dir}/*.wav')))
print(len(files))
pred=model.transcribe(paths2audio_files=files, batch_size=8)

10359
[NeMo I 2020-10-15 00:51:16 collections:173] Dataset loaded with 10359 files totalling 287750.00 hours
[NeMo I 2020-10-15 00:51:16 collections:174] 0 files were filtered totalling 0.00 hours


In [8]:
model.train()

EncDecCTCModel(
  (preprocessor): AudioToMelSpectrogramPreprocessor(
    (featurizer): FilterbankFeatures()
  )
  (encoder): ConvASREncoder(
    (encoder): Sequential(
      (0): JasperBlock(
        (mconv): ModuleList(
          (0): MaskedConv1d(
            (conv): Conv1d(64, 64, kernel_size=[33], stride=[2], padding=(16,), dilation=[1], groups=64, bias=False)
          )
          (1): MaskedConv1d(
            (conv): Conv1d(64, 256, kernel_size=(1,), stride=(1,), bias=False)
          )
          (2): BatchNorm1d(256, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
        )
        (mout): Sequential(
          (0): ReLU()
          (1): Dropout(p=0.0, inplace=False)
        )
      )
      (1): JasperBlock(
        (mconv): ModuleList(
          (0): MaskedConv1d(
            (conv): Conv1d(256, 256, kernel_size=[33], stride=[1], padding=(16,), dilation=[1], groups=256, bias=False)
          )
          (1): MaskedConv1d(
            (conv): Conv1d(256, 256, ke

In [5]:
import pandas as pd
pd.DataFrame(pred

0
0      ቸዘቸኔዘፌኔዘኔሁፌኔዘርኢዘሶዘዮሁኦኔሁዘጢኼኦዛኔሳሁኦኔዶሏዛርኔኜቸጵዘሁኦኜዘ...
1      ዘቸኔፌኔሁፌኔዘሚሶርዘፒዮሶሁኸዛዮሳጋስሒዮፌኔጾኔዘኙዷዛሁሶፌዮኜሶጻሁሳኔልሊር...
2      ዘቸዘቸኜይኦይኜዘ ኞቾኔዘቡሺኜሳቾፋሳኜዘኜሳኜቆሁቡሀዘሹዘሁኦቭልቡኼቆርጂቡሁኞ...
3      ቸኔኜኼሦፌተኔሀለሁሦኜዮሀኙኔጊኼፕቾኜሁሶሀኙጊዶኼኸጂዮሀጊይኼቾኜኞሀፎዐሁፌይኞ...
4      ዘቸዘፌዘኔሺዛሁሹዛልሣዛሎኪሶኸኢኼኔሽሁፌሁቭፌኞፌኜዮሀሁዛሁርጳሁዮታርኦኔዮኔሁ...
...                                                  ...
10354  ዘቸዘቸዘቸኔችኜፌኔዶኼርጂቆኔጓቡልቁሁርኦሁዛኔሁኔልቁ ሶዬኔጻረዚሁሶኸዕሯሽሁኦ...
10355  ቸዘቸዘቸሁኔዘፌኞፌኔሺሁሴኸኔዘሶሁኦሳኔላኼኸዷሀዛሁኸላዘሁፌዛኔዘፌኔዘጋጿለሀዘ...
10356                                ዘቸዘኔዘፌኔዘሊፕዓኔዛኔሑሁፌኔጋ
10357  ቸኜጊኼሒፌኜኔሀኋይውፕኋፌኔሡኋውኼኋይኔኋዘይለዐለኔለቭሦኜኔሦውተሦውኔዘቾኔዘኔ...
10358  ቸዘቸዘቸኔቸኔፌኜየኦዮጾዮሳፌኜፌኜቄሁፌሁፎሁፌኔፌሁፌዷቄለቭኚኔዘኔሁፌዛሶሁሎዛ...

[10359 rows x 1 columns]

In [7]:
import numpy as np
np.mean([len(x) for x in pred])

144.8206390578241